In [ ]:
import datetime
import pandas as pd
import serenitas.analytics
import numpy as np

from pandas.tseries.offsets import BDay, BMonthEnd
from serenitas.analytics.scenarios import run_portfolio_scenarios
from risk.portfolio import build_portfolio, generate_vol_surface
from pathlib import Path

from serenitas.analytics.index_data import load_all_curves
from serenitas.utils.db import serenitas_pool

In [ ]:
run_date = datetime.date.today()
serenitas.analytics._local = False
base_dir = Path('/home/serenitas/Daily/Risk/')

### Run credit spread scenarios

In [ ]:
scenarios = []
for position_date in pd.date_range((datetime.date.today() - BMonthEnd(2)), (datetime.date.today() - BMonthEnd(1)), freq="BM"):
    spread_date = position_date
    spread_shock = np.array([-100., -25., 1., +25. , 100.])
    serenitas.analytics.init_ontr(spread_date)
    spread_shock /= serenitas.analytics._ontr['HY'].spread
    portf, _ = build_portfolio(position_date.date(), spread_date.date())
    vol_surface = generate_vol_surface(portf, 5)
    portf.reset_pv()
    scens = run_portfolio_scenarios(portf, date_range=[pd.Timestamp(spread_date)], params=['pnl'],
                                    spread_shock=spread_shock,
                                    vol_shock= [0.0],
                                    corr_shock=[0.0],
                                    vol_surface=vol_surface)
    scenarios.append(scens.sum(axis=1))
pd.concat(scenarios).to_csv(base_dir / f"csscen_{run_date:%Y%m%d}.csv")

### Jump to default

In [ ]:
for position_date in pd.date_range((datetime.date.today() - BMonthEnd(12)), (datetime.date.today() - BMonthEnd(1)), freq="BM"):
    spread_date = position_date
    _, portf = build_portfolio(position_date.date(), spread_date.date())
    jtd = portf.jtd_single_names()
    conn = serenitas_pool.getconn()
    surv_curves = load_all_curves(conn, spread_date.date())
    serenitas_pool.putconn(conn)
    surv_curves['spread'] = surv_curves['curve'].apply(lambda sc: sc.to_series(forward=False)[5] * (1-sc.recovery_rates[5]))
    jtd_sabo = jtd[[jtd.columns[0]]].join(surv_curves.groupby(level=0).first()[['name', 'company_id', 'spread']])
    jtd_sabo.columns = ['jtd', 'name', 'company_id', 'spread']
    jtd_sabo = jtd_sabo.groupby(['company_id', 'name']).sum()
    jtd_sabo.to_csv(base_dir / f"jtd_{position_date:%Y%m%d}.csv")